# Import a Dataset Into Jupyter

## importing libraries…

In [27]:
# Importing libraries
import pandas as pd
import numpy as np

import time, sys
from IPython.display import clear_output
from pathlib import Path 
import os

import matplotlib

from statsmodels.tsa.seasonal import seasonal_decompose

# plotly packages
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.offline import iplot
import plotly.tools as tls
from plotly.subplots import make_subplots

## Specify URL

can set limit in the url
eg: url = 'https://data.cityofchicago.org/resource/sxs8-h27x.json?time=2019-02-26T04:20:51.000'
https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=time%20between%20%272018-03-02T00:00:00%27%20and%20%272019-09-30T00:00:00%27&segment_id=158&where=speed%20%3E%20-1

can use Socrata Query Language: https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=time between '2020-01-10T12:00:00' and '2021-01-10T14:00:00'

HTML URL Encoding:
| Character | From Windows-1252 | From UTF-8 |
| --- | --- | --- |
| space | %20 | %20 |
| ' | %27 | %27 |

url = 'https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=time%20between%20%272020-01-10T12:00:00%27%20and%20%272021-01-10T14:00:00%27'

## Choosing a road segment

Print out all road segment

In [28]:
segment_id_set=pd.read_json('https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=time%20between%20%272018-03-05T00:00:00%27%20and%20%272018-03-07T00:00:00%27&$select=distinct%20segment_id&$limit=50000')

In [29]:
unique_segment_id=[]
# using iteritems() function to retrieve rows
for value in segment_id_set.itertuples():
    unique_segment_id.append(value[1])
unique_segment_id.sort()
print(unique_segment_id)
print(len(unique_segment_id))

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 129, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 166, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 214, 215, 216, 217, 218, 219, 220, 221, 222, 223, 224, 225, 226, 227, 228, 229, 230, 

## Page through data

| Query Parameter | Description | Default Value | Maximum Value |
| --- | --- | --- | --- |
| $limit | The number of results to return | 1000 | 50,000 |
| $offset | The index of the result array where to start the returned list of results. | 0 | N/A |

The order of the results of a query are not implicitly ordered, so if you're paging, make sure you provide an $order clause or at a minimum $order=:id. That will guarantee that the order of your results will be stable as you page through the dataset.

eg:
1) get the first 5 results: 'https://soda.demo.socrata.com/resource/earthquakes.json?$limit=5&$offset=0&$order=earthquake_id'

2) retrieve the next five results: 'https://soda.demo.socrata.com/resource/earthquakes.json?$limit=5&$offset=5&$order=earthquake_id'

In [30]:
def page_through_data(segment_id,start_time,end_time):

    '''
    Name of Function: page_through_data
    Purpose of Function: to read the traffic data page by page
    Inputs: 
            -segment_id
            -start_time
            -end_time
    Expected Outputs: 
            -segment_id_xxxx_df
    ''' 

    # The $offset is the number of records into a dataset that you want to start, indexed at 0.
    offset  = 0 # start with no offset
    # segment_id = i #choose a road segment
    df_list = []
    data = pd.read_json(f"https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=speed!=-1%20AND%20time%20between%20%27{start_time}%27%20and%20%27{end_time}%27&segment_id={segment_id}&$limit=50000&$offset={offset}&$order=time")
    #Notice the speed!=-1 condition specified in the url, it can help get rid of empty data
    while len(data)==50000: #check num of rows in each page, if num of rows == maximum value for $limit, next page exist
        df_list.append(data) #append data to the list
        offset = offset + 50000 #move to next page
        data = pd.read_json(f"https://data.cityofchicago.org/resource/sxs8-h27x.json?$where=speed!=-1%20AND%20time%20between%20%27{start_time}%27%20and%20%27{end_time}%27&segment_id={segment_id}&$limit=50000&$offset={offset}&$order=time")
    df_list.append(data)
    globals()['segment_id_'+str(segment_id) + '_df'] = pd.concat(df_list) #merge data into one dataset

In [31]:
segment_id = 1268
page_through_data(segment_id,'2018-03-05T00:00:00','2021-03-05T00:00:00')

In [32]:
globals()['segment_id_'+str(segment_id) + '_df'].head()

time  segment_id  speed   street direction from_street  \
0  2018-03-05T00:10:25.000        1268     28  Indiana        SB       127th   
1  2018-03-05T00:40:09.000        1268     28  Indiana        SB       127th   
2  2018-03-05T01:10:27.000        1268     28  Indiana        SB       127th   
3  2018-03-05T01:40:06.000        1268     28  Indiana        SB       127th   
4  2018-03-05T02:10:20.000        1268     28  Indiana        SB       127th   

  to_street    length street_heading             comments  ...  hour  \
0     130th  0.297679              S  Outside City Limits  ...     0   
1     130th  0.297679              S  Outside City Limits  ...     0   
2     130th  0.297679              S  Outside City Limits  ...     1   
3     130th  0.297679              S  Outside City Limits  ...     1   
4     130th  0.297679              S  Outside City Limits  ...     2   

   day_of_week  month          record_id  start_latitude start_longitude  \
0            2      3  1268-201803050610       41.663309      -87.617866   
1            2      3  1268-201803050640       41.663309      -87.617866   
2            2      3  1268-201803050710       41.663309      -87.617866   
3            2      3  1268-201803050740       41.663309      -87.617866   
4            2      3  1268-201803050810       41.663309      -87.617866   

   end_latitude  end_longitude  \
0     41.659006     -87.618769   
1     41.659006     -87.618769   
2     41.659006     -87.618769   
3     41.659006     -87.618769   
4     41.659006     -87.618769   

                                      start_location  \
0  {'type': 'Point', 'coordinates': [-87.617866, ...   
1  {'type': 'Point', 'coordinates': [-87.617866, ...   
2  {'type': 'Point', 'coordinates': [-87.617866, ...   
3  {'type': 'Point', 'coordinates': [-87.617866, ...   
4  {'type': 'Point', 'coordinates': [-87.617866, ...   

                                        end_location  
0  {'type': 'Point', 'coordinates': [-87.618769, ...  
1  {'type': 'Point', 'coordinates': [-87.618769, ...  
2  {'type': 'Point', 'coordinates': [-87.618769, ...  
3  {'type': 'Point', 'coordinates': [-87.618769, ...  
4  {'type': 'Point', 'coordinates': [-87.618769, ...  

[5 rows x 22 columns]

## Resample the data

Downsample the series into 1hr bins and find the maximum speed of the timestamps falling into a bin.

In [33]:
def resample_data(segment_id):

    '''
    Name of Function: resample_data
    Purpose of Function: downsample the traffic data
    Inputs:
            -segment_id
    Expected Outputs:
            -segment_id_xxxx_resample
    ''' 

    globals()['segment_id_'+str(segment_id) + '_df'].index = pd.to_datetime(globals()['segment_id_'+str(segment_id) + '_df'].time) # transform the time column into an actual date object and set it as index
    globals()['segment_id_'+str(segment_id) + '_resample']= pd.DataFrame()
    globals()['segment_id_'+str(segment_id) + '_resample']['speed']=globals()['segment_id_'+str(segment_id) + '_df'].speed.resample('24H').max()
    #interpolate missing values
    globals()['segment_id_'+str(segment_id) + '_resample']['speed']=globals()['segment_id_'+str(segment_id) + '_resample']['speed'].interpolate(method='linear', limit_direction='both')
    
    # fig = make_subplots(rows=2, cols=1,subplot_titles=["Original", "Resampled"],shared_xaxes=True)
    # fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_df'].index, y=globals()['segment_id_'+str(segment_id) + '_df'].speed, mode='lines'),row=1, col=1,)
    # fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_resample'].index, y=globals()['segment_id_'+str(segment_id) + '_resample'].speed, mode='lines'),row=2, col=1,)

    # fig.update_layout(height=900, margin=dict(t=100), showlegend=False)
    # fig.show()

resample_data(segment_id)

In [34]:
globals()['segment_id_'+str(segment_id) + '_resample'].head()

speed
time             
2018-03-05   38.0
2018-03-06   35.0
2018-03-07   38.0
2018-03-08   38.0
2018-03-09   35.0

In [35]:
fig = make_subplots(rows=2, cols=1,subplot_titles=["Original", "Resampled"],shared_xaxes=True)
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_df'].index, y=globals()['segment_id_'+str(segment_id) + '_df'].speed, mode='lines'),row=1, col=1,)
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_resample'].index, y=globals()['segment_id_'+str(segment_id) + '_resample'].speed, mode='lines'),row=2, col=1,)

fig.update_layout(height=900, margin=dict(t=100), showlegend=False)
fig.show()

## Time Series Decomposition 

Decompose time series into trend, seasonal, and residual components
- Trend — general movement over time
- Seasonal — behaviors captured in individual seasonal periods
- Residual — everything not captured by trend and seasonal components

The additive model is Y[t] = T[t] + S[t] + r[t]

The results are obtained by first estimating the trend by applying a convolution filter to the data. The trend is then removed from the series and the average of this de-trended series for each period is the returned seasonal component.

To get rid of the predictable congestion, we only use the residual part

In [36]:
def decompose(segment_id):
    """
    A function that returns the trend, seasonality and residual captured by applying additive model.
    Inputs:
            -segment_id
    Expected Outputs:
            -segment_id_xxxx_decompose
    """
    globals()['segment_id_'+str(segment_id) + '_decompose'] = seasonal_decompose(globals()['segment_id_'+str(segment_id) + '_resample']['speed'], model = 'additive')

#     fig = make_subplots(rows=4, cols=1,subplot_titles=["Observed", "Trend", "Seasonal", "Residuals"])
#     fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].observed.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].observed, mode='lines'),row=1, col=1,)
#     fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].trend.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].trend, mode='lines'),row=2, col=1,)
#     fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].seasonal.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].seasonal, mode='lines'),row=3, col=1,)
#     fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].resid.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].resid, mode='lines'),row=4, col=1,)
#     fig.update_layout(height=900, margin=dict(t=100), showlegend=False)
#     fig.update_xaxes(showticklabels=False) # hide all the xticks
#     fig.update_xaxes(showticklabels=True, row=4, col=1)
#     fig.show()

decompose(segment_id)

In [37]:
globals()['segment_id_'+str(segment_id) + '_decompose'].resid.head(20)

time
2018-03-05         NaN
2018-03-06         NaN
2018-03-07         NaN
2018-03-08    1.437228
2018-03-09   -1.644686
2018-03-10    3.262900
2018-03-11   -3.759002
2018-03-12    1.520195
2018-03-13   -2.138409
2018-03-14    1.893203
2018-03-15    2.580085
2018-03-16    2.926743
2018-03-17   -4.879958
2018-03-18   -2.473288
2018-03-19    1.091624
2018-03-20   -1.138409
2018-03-21   -0.106797
2018-03-22    1.437228
2018-03-23    3.641028
2018-03-24   -0.451386
Freq: 24H, Name: resid, dtype: float64

In [38]:
fig = make_subplots(rows=4, cols=1,subplot_titles=["Observed", "Trend", "Seasonal", "Residuals"])
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].observed.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].observed, mode='lines'),row=1, col=1,)
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].trend.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].trend, mode='lines'),row=2, col=1,)
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].seasonal.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].seasonal, mode='lines'),row=3, col=1,)
fig.add_trace(go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_decompose'].resid.index, y=globals()['segment_id_'+str(segment_id) + '_decompose'].resid, mode='lines'),row=4, col=1,)
fig.update_layout(height=900, margin=dict(t=100), showlegend=False)
fig.update_xaxes(showticklabels=False) # hide all the xticks
fig.update_xaxes(showticklabels=True, row=4, col=1)
fig.show()

## Calculate Speed Reduction Index (SRI)

SRI = (1-Vac/Vff)*10

where consider the 85th percentile of the speed as the free-flow speed

In [39]:
def SRI_Cal(segment_id):
    
    '''
    Name of Function: SRI_Cal
    Purpose of Function: SRI calculation
        Inputs:
            -segment_id
    Expected Outputs:
            -segment_id_xxxx_resample
    '''    
    
    minimum = globals()['segment_id_'+str(segment_id) + '_decompose'].resid.min()
    resid = globals()['segment_id_'+str(segment_id) + '_decompose'].resid.subtract(minimum) #offset resid to all positive number
    quatile = resid.quantile(q=0.85) #calculate 85th percentile of the speed
    globals()['segment_id_'+str(segment_id) + '_resample']['SRI']= (1-resid/quatile)*10
    # Notice here the SRI is stored in segment_id_xxx_resample

#     fig = go.Figure(data=go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_resample'].index , y=globals()['segment_id_'+str(segment_id) + '_resample'].SRI, mode='markers'), layout = go.Layout(xaxis_title="time",yaxis_title="SRI"))
#     fig.show()

SRI_Cal(segment_id)

In [40]:
globals()['segment_id_'+str(segment_id) + '_resample'].head(20)

speed       SRI
time                       
2018-03-05   38.0       NaN
2018-03-06   35.0       NaN
2018-03-07   38.0       NaN
2018-03-08   38.0  1.635677
2018-03-09   35.0  4.682721
2018-03-10   38.0 -0.169338
2018-03-11   29.0  6.773115
2018-03-12   38.0  1.553649
2018-03-13   35.0  5.170859
2018-03-14   38.0  1.184861
2018-03-15   38.0  0.505751
2018-03-16   38.0  0.163015
2018-03-17   28.0  7.881388
2018-03-18   28.0  5.501948
2018-03-19   35.0  1.977371
2018-03-20   33.0  4.182173
2018-03-21   35.0  3.162232
2018-03-22   36.0  1.635677
2018-03-23   38.0 -0.543189
2018-03-24   32.0  3.502923

In [41]:
fig = go.Figure(data=go.Scatter(x=globals()['segment_id_'+str(segment_id) + '_resample'].index , y=globals()['segment_id_'+str(segment_id) + '_resample'].SRI, mode='lines'), layout = go.Layout(xaxis_title="time",yaxis_title="SRI"))
fig.show()

Notice the NaN in the SRI column for the very begining and end og the time serie

## Calculate SRI for all road Segment

In [ ]:
# use a function to show progress
def update_progress(progress):
    bar_length = 100
    if isinstance(progress, int):
        progress = float(progress)
    if not isinstance(progress, float):
        progress = 0
    if progress < 0:
        progress = 0
    if progress >= 1:
        progress = 1
    block = int(round(bar_length * progress))

    clear_output(wait = True)
    text = "Progress: [{0}] {1:.1f}%".format( "#" * block + "-" * (bar_length - block), progress * 100)
    print(text)

# This cell may take 8 hr to finish
# Can change the for loop to only calculate few road segments
i = 0
for segment_id in unique_segment_id:
    if os.path.exists(Path('SRI/' + str(segment_id) + '_SRI.csv')): #check if SRI fila already exist in the SRI folder
        i = i+1
        update_progress(i / len(unique_segment_id))
    else:
        page_through_data(segment_id,'2018-03-05T00:00:00','2021-03-05T00:00:00')
        if len(globals()['segment_id_'+str(segment_id) + '_df'])==0:
            i=i+1
            update_progress(i / len(unique_segment_id))
        else:
            resample_data(segment_id)
            decompose(segment_id)
            SRI_Cal(segment_id)
            filepath = Path('SRI/' + str(segment_id) + '_SRI.csv')
            globals()['segment_id_'+str(segment_id) + '_resample'].to_csv(filepath)
            lst = [globals()['segment_id_'+str(segment_id) + '_df'], globals()['segment_id_'+str(segment_id) + '_resample'], globals()['segment_id_'+str(segment_id) + '_decompose']]
            del globals()['segment_id_'+str(segment_id) + '_df'], globals()['segment_id_'+str(segment_id) + '_resample'], globals()['segment_id_'+str(segment_id) + '_decompose'] # delete dataframe
            del lst # memory release
            i=i+1
            update_progress(i / len(unique_segment_id))

Progress: [##########------------------------------------------------------------------------------------------] 9.7%
